# Basic Example: Train a MOFA model

This notebook shows a simple way to train a MOFA [1] model with additional sparsity priors. We use a chronic lymphocytic leukaemia (CLL) data set, which combined ex vivo drug response measurements with somatic mutation status, transcriptome profiling and DNA methylation assays [2].

[1] Multi-Omics Factor Analysis-a framework for unsupervised integration of multi-omics data sets by Argelaguet, R. et al. (2018)  
[2] Drug-perturbation-based stratification of blood cancer by Dietrich et al. (2018)

In [2]:
import scanpy as sc
from data_loader import load_CLL
from famo.core import CORE
from famo.plotting import (
    plot_factor,
    plot_factor_correlation,
    plot_top_weights,
    plot_training_curve,
    plot_variance_explained,
    plot_weights,
)

## Load and Preprocess Data

In [3]:
# Load CLL data
mdata = load_CLL()

# Normalize and log transform mRNA counts
sc.pp.normalize_total(mdata["mrna"], target_sum=1e4)
sc.pp.log1p(mdata["mrna"])

/Users/martin/miniconda3/envs/famo/lib/python3.12/site-packages/anndata/_core/anndata.py:430: FutureWarning: The dtype argument is deprecated and will be removed in late 2024.
  warnings.warn(
/Users/martin/miniconda3/envs/famo/lib/python3.12/site-packages/anndata/_core/anndata.py:430: FutureWarning: The dtype argument is deprecated and will be removed in late 2024.
  warnings.warn(
/Users/martin/miniconda3/envs/famo/lib/python3.12/site-packages/anndata/_core/anndata.py:430: FutureWarning: The dtype argument is deprecated and will be removed in late 2024.
  warnings.warn(
/Users/martin/miniconda3/envs/famo/lib/python3.12/site-packages/anndata/_core/anndata.py:430: FutureWarning: The dtype argument is deprecated and will be removed in late 2024.
  warnings.warn(



## Example 1: Run Factor Analysis

In a first experiment, we will just use all four views and run the factorization. Each experiment consists of two necessary steps:

1) Create a new model instance: `model = CORE()`
3) Train the model: `model.fit(n_factors=15, data=mdata)`

To make your life simple, we only require you to specify the number of factors. In Example 2, we will show you how to deviate from the default parameters and customize your model. For simplicity we will model all data with a Gaussian noise model.
In contrast to the original MOFA definition, we place a Horseshoe sparsity prior [3] on the weights.

[3] Carvalho, Carlos M., Nicholas G. Polson, and James G. Scott. "Handling sparsity via the horseshoe." Artificial intelligence and statistics. PMLR, 2009.

In [5]:
# Run model with MuData object
model = CORE(device="cuda")
model.fit(
    data=mdata,
    n_factors=15,
    likelihoods={
        "mrna": "Normal",
        "drugs": "Normal",
        "mutations": "Normal",
        "methylation": "Normal",
    },
    factor_prior="Normal",
    weight_prior="Horseshoe",
)

Setting up device...
- `cuda` not available...
- Running all computations on `cpu`
Fitting model...
- Checking compatibility of provided likelihoods with data.
  - mrna: Normal
  - drugs: Normal
  - mutations: Normal
  - methylation: Normal
- Centering group_1/drugs...
- Centering group_1/methylation...
- Centering group_1/mrna...
- Centering group_1/mutations...


alt.Chart(...)

Initializing factors using `random` method...
Epoch:       0 | Time:       0.98s | Loss: 3502104.52
Epoch:     500 | Time:      61.34s | Loss: 3007700.71
Epoch:    1000 | Time:     115.25s | Loss: 2779518.16
Epoch:    1500 | Time:     167.61s | Loss: 2624194.54
Epoch:    2000 | Time:     220.75s | Loss: 2522245.70
Epoch:    2500 | Time:     272.47s | Loss: 2455518.35
Epoch:    3000 | Time:     324.87s | Loss: 2400859.31
Epoch:    3500 | Time:     376.83s | Loss: 2377852.37
Epoch:    4000 | Time:     428.26s | Loss: 2361380.91
Epoch:    4500 | Time:     486.75s | Loss: 2345399.91
Epoch:    5000 | Time:     542.93s | Loss: 2335549.65


## Plot Results

After training, we can inspect all learned parameters, visualize the loss curve, etc.


### ELBO

In [4]:
# Plot training curve
plot_training_curve(model)

alt.Chart(...)

### Plot a heatmap of the weights

To perform downstream analysis, we need to extract the factor loadings and weights from the model. We can do this by calling the `get_factors()` and `get_weights()` method. This returns a dictionary with the weights for each modality and factors (for each group) respectively.


In [5]:
# Get learned model parameters
factors = model.get_factors()
weights = model.get_weights()

In [ ]:
import altair as alt

# def plot_factors(factors, color_by):
# Make a plot of factors colored by a given variable
# x: variable
# y: factor value
factors = model.get_factors(return_type="anndata")
covariate =

However, we also provide functionality to plot the weights directly.

In [6]:
# Plot learned weights
plot_weights(model)

alt.HConcatChart(...)

### Factor Correlation Matrix

In [7]:
plot_factor_correlation(model)

alt.HConcatChart(...)

### Variance Explained Plot

In [8]:
plot_variance_explained(model)

alt.HConcatChart(...)

### Factor Values

In [9]:
plot_factor(model, factor=1)

alt.VConcatChart(...)

### Top weights per factor

In [10]:
plot_top_weights(model, view="mutations", factor=[1, 3], orientation="horizontal")

alt.HConcatChart(...)